## Audio Feature Selection with Librosa

# Goals for Week 1 of AI Mentor Project

#### 1. Understand Librosa and how audio feature extraction can work and which are important for our setup.

#### 2. Understand how we can compare 2 audio files on a global scale that might be different lengths across dimensions of: EQ, Energy, Rhythm

#### 3. Understand how we can compare 2 chorus sections perhaps with the same or different lengths across different audio dimensions

#### 4. Setup a very simple RAG retrival against 5 data entries and see howe we can retry audio similarities on a very basic level.

#### 5. Once we have a retrival, use the basic user prompt to then output something form our text retrival that looks like basic global feedback. We can use Chat GPT API here as a baseline perhaps to keep it simple.



In [4]:
!pip install librosa --quiet

# Aim - Look at Global Feature extraction

In [2]:
# Steps to consider to better understand how we can use Librosa for our audio featues for the RAG.

# 1. How can I extract global audio features from an audio file
# 2. Which audio features give the best info on (rhythm, eq and energy and can help us with similarity matching)
# 3. How can I compare 2 audio files with embeddings? AND also just their audio features, what info does it tell me on a global setting?
# 4. How can I compare 2 chorus sections with the above methods, what does that tell me?


# 5. Does chunking have any effect here?

#
Mount Drive

In [5]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [6]:
from IPython.display import Audio, display
import os

def play_audio(file_path, show_controls=True):
    """Create an inline audio player in Jupyter"""
    if os.path.exists(file_path):
        print(f"🎵 Playing: {os.path.basename(file_path)}")
        display(Audio(file_path, autoplay=False))
    else:
        print(f"❌ File not found: {file_path}")

In [7]:
from pathlib import Path
import librosa

folder_path = Path('/content/drive/MyDrive/DSR-AI-MENTOR/AudioFeatureTest-1/')

# techno sketches
sketch_track_path = 'Sketch--2025-07-21 Nik Fury Remix.mp3'
sketch_track2_path = 'Sketch--2025-08-21 Nik Fury Remix.mp3'
long_sketch_path = '2025-05-15 pulse transfer.wav'

#broken beat sketch
broken_drum_sketch_path = 'africandrumarp 3.44 - eq strings on drop, down with shaker a bit, add more sub.wav'

# Repetitive techno track to use as reference track comparison
reference_track_path = 'Reftrack--M-High - The Saw That Broke The Camels Back (KiNK Dub Remix).mp3'
min_reference_track_path = 'Reftrack-1min-The Saw That Broke the Camels Back (KiNK Remix) - 1min snippet.mp3'

# Distinctly different genres as a check against similarity
med_track_path = 'AMBIENT-short-crystal-bowls.mp3'
piano_track_path = 'debussy-clair-de-lune.mp3'


In [8]:
from pathlib import Path
import librosa

# Sketches
full_path = folder_path / sketch_track_path # techno w vocal - sketch
full_path2 = folder_path / sketch_track2_path # techno w vocal - sketch V2 of same track
full_path3 = folder_path / long_sketch_path  # electro techno sketch
full_path4 = folder_path / broken_drum_sketch_path # house with broken african drums

# Classical Reference
full_path5 = folder_path / piano_track_path # clair de lune

# Motr varied full tracks for future testing
full_path6 = folder_path / '16 Faces - Held in infinite.wav' # Ambient Electronic
full_path7 = folder_path / 'Actress & London Contemporary Orchestra - N.mp3' # Electronic Classical
full_path8 = folder_path / 'Larkhaul Paul - Silent the Voice.wav' # Dnb
full_path9 = folder_path / '02-Baalti-Overbit.mp3' # indian drum broken
full_path10 = folder_path / '02_Insomniast - Higher.mp3' # tech house
full_path11 = folder_path / 'Ramadanman - Work Them___ref4chasingstreams.mp3' # 808 Bass

ref_full_path = folder_path / reference_track_path # techno ref track
short_ref_full_path = folder_path / min_reference_track_path # shorter version of techno reference

# singing bowl ref track - ambient with no drums
med_full_path = folder_path / med_track_path

# HOW TO LOAD INTO LIBROSA
y, sr = librosa.load(full_path, sr=None)
full_path

PosixPath('/content/drive/MyDrive/DSR-AI-MENTOR/AudioFeatureTest-1/Sketch--2025-07-21 Nik Fury Remix.mp3')

In [9]:
print(y) #amplitude array ouput
print(sr) #sample rate of original file

[0.000000e+00 0.000000e+00 0.000000e+00 ... 9.705850e-06 7.422944e-06
 7.755023e-06]
44100


# Extracting A Large Range of Global Features

### Although global audio features are likely to not give us the best info its a good starting point to understand which features might be useful here, and to set a baseline for how our similarity search will work which we can improve on

In [10]:
import librosa
import numpy as np
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics.pairwise import cosine_similarity
import warnings
warnings.filterwarnings("ignore")

def extract_global_features(audio_file, max_duration=600):
    """
    Extract global (whole-track) features for comparison.
    No segmentation - just overall track characteristics.
    """

    # Load audio
    sr = 22050
    hop_length = 128
    y, _ = librosa.load(audio_file, sr=sr)

    if max_duration:
        max_samples = int(max_duration * sr)
        y = y[:max_samples]

    # Extract harmonic and rhythmic material
    duration = float(librosa.get_duration(y=y, sr=sr))
    y_harm, y_perc = librosa.effects.hpss(y)

    # =================================================================
    # GLOBAL RHYTHM FEATURES - rhythmic content
    # =================================================================

    # Tempo and beat consistency
    tempo, beats = librosa.beat.beat_track(y=y_perc, sr=sr, hop_length=hop_length)
    tempo = float(tempo)

    # Onset analysis
    onset_env = librosa.onset.onset_strength(y=y_perc, sr=sr, hop_length=hop_length)
    onsets = librosa.onset.onset_detect(onset_envelope=onset_env, sr=sr, hop_length=hop_length)
    onset_times = librosa.frames_to_time(onsets, sr=sr, hop_length=hop_length)

    # Rhythmic complexity metrics
    if len(onset_times) > 1:
        intervals = np.diff(onset_times)
        beat_duration = 60.0 / tempo
        beat_relative = intervals / beat_duration
        syncopation = np.mean(np.abs(beat_relative - np.round(beat_relative)))
        rhythmic_variance = np.var(intervals)
        onset_density = len(onset_times) / duration
    else:
        syncopation = 0
        rhythmic_variance = 0
        onset_density = 0

    rhythm_features = {
        'tempo': tempo,
        'onset_density': onset_density,  # onsets per second
        'syncopation_level': syncopation,
        'rhythmic_variance': rhythmic_variance,
        'beat_strength': np.mean(onset_env)
    }

    # =================================================================
    # GLOBAL HARMONIC FEATURES - melody and harmonic content
    # =================================================================

    # Chroma analysis
    chroma = librosa.feature.chroma_cqt(y=y_harm, sr=sr, hop_length=hop_length)
    chroma_mean = np.mean(chroma, axis=1)

    # Key strength and harmonic complexity
    key_strength = np.max(chroma_mean) / (np.mean(chroma_mean) + 1e-8)
    chroma_variance = np.var(chroma, axis=1).mean()

    # Harmonic change rate
    chroma_diff = np.diff(chroma, axis=1)
    harmonic_change_rate = np.mean(np.sum(np.abs(chroma_diff), axis=0)) / duration

    harmonic_features = {
        'chroma_variance': chroma_variance,  # Overall harmonic complexity
        'key_strength': key_strength,       # How defined the key is
        'harmonic_change_rate': harmonic_change_rate,  # Changes per second
        'tonal_stability': 1.0 - np.std(chroma_mean)  # How stable the tonality is
    }

    # =================================================================
    # GLOBAL ENERGY FEATURES - Loudness and amplitude overtime
    # =================================================================

    # Energy dynamics
    rms = librosa.feature.rms(y=y, hop_length=hop_length)[0]
    energy_range = np.max(rms) - np.min(rms)
    avg_energy = np.mean(rms)


    # Energy curve shape
    energy_trend = np.polyfit(range(len(rms)), rms, 1)[0]  # Slope of energy over time

    # Peak analysis
    from scipy.signal import find_peaks
    peaks, _ = find_peaks(rms, height=np.mean(rms))
    peak_density = len(peaks) / duration

    energy_features = {
        'energy_range': energy_range,       # Dynamic range
        'avg_energy': avg_energy,           # Overall loudness
        'energy_trend': energy_trend,       # Building vs fading
        'peak_density': peak_density        # Energy peaks per second
    }

    # =================================================================
    # GLOBAL SPECTRAL FEATURES - EQ shape and Brightness
    # =================================================================

    # Overall spectral characteristics
    centroid = librosa.feature.spectral_centroid(y=y, sr=sr, hop_length=hop_length)[0]
    rolloff = librosa.feature.spectral_rolloff(y=y, sr=sr, hop_length=hop_length)[0]
    bandwidth = librosa.feature.spectral_bandwidth(y=y, sr=sr, hop_length=hop_length)[0]

    spectral_features = {
        'avg_brightness': np.mean(centroid),      # Average spectral centroid
        'brightness_variance': np.var(centroid),  # How much brightness changes
        'avg_rolloff': np.mean(rolloff),         # Average rolloff frequency
        'avg_bandwidth': np.mean(bandwidth),     # Average spectral width
    }

    # =================================================================
    # FREQUENCY BAND ANALYSIS - overall frequency bands
    # =================================================================

    # Frequency content analysis
    S = np.abs(librosa.stft(y, hop_length=hop_length))
    freqs = librosa.fft_frequencies(sr=sr)

    # Define frequency bands
    low_band = (freqs >= 20) & (freqs <= 250)     # Bass/kick
    mid_band = (freqs >= 250) & (freqs <= 2000)   # Vocals/snares
    high_band = (freqs >= 2000) & (freqs <= 8000) # Cymbals/air

    # Calculate average energy in each band
    low_energy = np.mean(S[low_band])
    mid_energy = np.mean(S[mid_band])
    high_energy = np.mean(S[high_band])

    total_energy = low_energy + mid_energy + high_energy

    frequency_features = {
        'low_proportion': low_energy / total_energy,
        'mid_proportion': mid_energy / total_energy,
        'high_proportion': high_energy / total_energy,
        'mid_low_ratio': mid_energy / (low_energy + 1e-8),
        'high_mid_ratio': high_energy / (mid_energy + 1e-8)
    }

    # =================================================================
    # COMBINE INTO GLOBAL SUMMARY
    # =================================================================

    global_analysis = {
        'metadata': {
            'duration': duration,
            'sample_rate': sr
        },
        'rhythm': rhythm_features,
        'harmony': harmonic_features,
        'energy': energy_features,
        'spectral': spectral_features,
        'frequency': frequency_features
    }

    return global_analysis

## WE OVER RIGHT THIS LATER SO I COMMENTED IT OUT TO AVOID COLAB USING IT

# def create_comparison_vector(analysis):
#     """Convert analysis to normalized vector for similarity comparison"""

#     # Extract key discriminating features
#     vector = np.array([
#         # Rhythm (normalized)
#         analysis['rhythm']['tempo'] / 200.0,  # Normalize tempo to 0-1
#         analysis['rhythm']['onset_density'],   # Already per-second
#         analysis['rhythm']['syncopation_level'],
#         analysis['rhythm']['rhythmic_variance'],

#         # Harmony
#         analysis['harmony']['chroma_variance'],
#         analysis['harmony']['key_strength'],
#         analysis['harmony']['harmonic_change_rate'],
#         analysis['harmony']['tonal_stability'],

#         # Energy
#         analysis['energy']['energy_range'],
#         analysis['energy']['avg_energy'],
#         analysis['energy']['energy_trend'],
#         analysis['energy']['peak_density'],

#         # Spectral
#         analysis['spectral']['avg_brightness'] / 8000.0,  # Normalize frequency
#         analysis['spectral']['brightness_variance'] / 1000000.0,

#         # Frequency balance
#         analysis['frequency']['low_proportion'],
#         analysis['frequency']['mid_proportion'],
#         analysis['frequency']['high_proportion'],
#         analysis['frequency']['mid_low_ratio'],
#         analysis['frequency']['high_mid_ratio']
#     ])

#     return vector

# def compare_global_features(track1_file, track2_file):
#     """Compare two tracks on global characteristics"""

#     print("Extracting global features...")
#     analysis1 = extract_global_features(track1_file)
#     analysis2 = extract_global_features(track2_file)

#     print(f"Track 1: {analysis1['metadata']['duration']:.1f}s")
#     print(f"Track 2: {analysis2['metadata']['duration']:.1f}s")

#     # Create comparison vectors
#     vector1 = create_comparison_vector(analysis1)
#     vector2 = create_comparison_vector(analysis2)

#     # Calculate similarity
#     similarity = cosine_similarity([vector1], [vector2])[0][0]

#     print(f"\n=== GLOBAL SIMILARITY: {similarity:.3f} ===")
#     print("(1.0 = identical, 0.0 = completely different)")

#     # Detailed feature comparison
#     print(f"\n=== DETAILED COMPARISON ===")

#     categories = ['rhythm', 'harmony', 'energy', 'spectral', 'frequency']

#     for category in categories:
#         print(f"\n{category.upper()}:")
#         features1 = analysis1[category]
#         features2 = analysis2[category]

#         for key in features1.keys():
#             val1 = features1[key]
#             val2 = features2[key]
#             diff = abs(val1 - val2)

#             if category == 'rhythm' and key == 'tempo':
#                 diff_pct = diff / max(val1, val2) * 100
#                 print(f"  {key}: {val1:.1f} vs {val2:.1f} (±{diff:.1f} BPM, {diff_pct:.1f}% diff)")
#             elif key in ['chroma_variance', 'energy_range', 'mid_low_ratio']:
#                 diff_pct = diff / max(val1, val2, 0.001) * 100 if max(val1, val2) > 0 else 0
#                 print(f"  {key}: {val1:.3f} vs {val2:.3f} (±{diff:.3f}, {diff_pct:.1f}% diff)")
#             else:
#                 print(f"  {key}: {val1:.3f} vs {val2:.3f} (±{diff:.3f})")

#     # Identify biggest differences
#     print(f"\n=== BIGGEST DIFFERENCES ===")
#     feature_names = [
#         'tempo', 'onset_density', 'syncopation_level', 'chroma_variance',
#         'energy_range', 'avg_brightness', 'mid_low_ratio'
#     ]

#     differences = []
#     for i, name in enumerate(feature_names):
#         if i < len(vector1):
#             diff = abs(vector1[i] - vector2[i])
#             differences.append((name, diff, vector1[i], vector2[i]))

#     # Sort by difference size
#     differences.sort(key=lambda x: x[1], reverse=True)

#     for name, diff, val1, val2 in differences[:5]:
#         print(f"  {name}: {val1:.3f} vs {val2:.3f} (diff: {diff:.3f})")

#     return {
#         'similarity': similarity,
#         'analysis1': analysis1,
#         'analysis2': analysis2,
#         'vector1': vector1,
#         'vector2': vector2,
#         'differences': differences
#     }

# Usage example:
# results = compare_global_features(full_path, ref_full_path)

# Lets compare a techno sketch to a short chunk from a finished mastered techno track

In [11]:
play_audio(full_path)
play_audio(short_ref_full_path)

🎵 Playing: Sketch--2025-07-21 Nik Fury Remix.mp3


🎵 Playing: Reftrack-1min-The Saw That Broke the Camels Back (KiNK Remix) - 1min snippet.mp3


In [ ]:
# techno work in progress track 1 min long
# track1_info = extract_global_features(full_path)
# print(track1_info)
# print('###')

# fully finished reference track, techno but only the first 1min of it.
# track2_info = extract_global_features(short_ref_full_path)
# print(track2_info)

# Lets look at some comparison metrics for our large set of extracted features.
results = compare_global_features(full_path, short_ref_full_path)

# Lets do the same with a different electronic track and the same reference short.

In [ ]:
play_audio(full_path4)
play_audio(short_ref_full_path)

In [ ]:
# broken beat track in progress track - a bit longer
# track1_info = extract_global_features(full_path4)
# print(track1_info)
print('###')

# fully finished reference track, techno but only the first 1min of it.
# track2_info = extract_global_features(short_ref_full_path)
# print(track2_info)

# Lets look at some comparison metrics for our large set of extracted features.
results = compare_global_features(full_path4, short_ref_full_path)

# And one last time comparing a classical piano track against our techno sketch

In [ ]:
play_audio(full_path5)
play_audio(short_ref_full_path)

In [ ]:
# Lets look at some comparison metrics for clair de lune VS techno sketch
results = compare_global_features(full_path5, short_ref_full_path)

We Appear to be getting simialarities that are crazy high, which is odd given the last comparison was between classical music and techno.

Im will look at limiting the features and doing a different normalization to see if this makes a difference.

# Handle Normalization smarter in our vector creation

In [12]:
from sklearn.preprocessing import StandardScaler

def create_comparison_vector(analysis):
    """Convert analysis to raw vector - normalization handled in compare function"""

    # Extract raw features (removed arbitrary scaling)
    vector = np.array([
        # Rhythm
        analysis['rhythm']['tempo'] / 200.0,                    # 0-200 BPM typical range
        analysis['rhythm']['onset_density'] / 15.0,             # 0-15 onsets/sec max observed
        analysis['rhythm']['syncopation_level'],                # Already 0-1 range
        analysis['rhythm']['rhythmic_variance'] / 0.1,          # 0-0.1 variance range

        # Harmony
        analysis['harmony']['chroma_variance'] / 0.1,           # 0-0.1 range
        analysis['harmony']['key_strength'] / 3.0,              # 0-3 range
        analysis['harmony']['harmonic_change_rate'] / 0.005,    # 0-0.005 range
        analysis['harmony']['tonal_stability'],                 # Already 0-1 range

        # Energy
        analysis['energy']['energy_range'],                     # Already 0-1 range
        analysis['energy']['avg_energy'],                       # Already 0-1 range
        abs(analysis['energy']['energy_trend']) / 0.001,        # Very small values, use abs
        analysis['energy']['peak_density'] / 25.0,              # 0-25 peaks/sec max

        # Spectral - these were the problem!
        analysis['spectral']['avg_brightness'] / 8000.0,        # 0-8kHz range
        analysis['spectral']['brightness_variance'] / 2000000.0, # 0-2M range (was dominating!)

        # Frequency balance
        analysis['frequency']['low_proportion'],                 # Already 0-1
        analysis['frequency']['mid_proportion'],                 # Already 0-1
        analysis['frequency']['high_proportion'],                # Already 0-1
        analysis['frequency']['mid_low_ratio']
        analysis['frequency']['high_mid_ratio']

    ])

    return vector


def compare_global_features(track1_file, track2_file):
    """Compare two tracks on global characteristics"""

    print("Extracting global features...")
    analysis1 = extract_global_features(track1_file)
    analysis2 = extract_global_features(track2_file)

    print(f"Track 1: {analysis1['metadata']['duration']:.1f}s")
    print(f"Track 2: {analysis2['metadata']['duration']:.1f}s")

    # Create comparison vectors
    vector1 = create_comparison_vector(analysis1)
    vector2 = create_comparison_vector(analysis2)

    # scaler = MinMaxScaler()
    # normalized_vectors = scaler.fit_transform([raw_vector1, raw_vector2])
    # vector1, vector2 = normalized_vectors[0], normalized_vectors[1]

    # Calculate similarity
    similarity = cosine_similarity([vector1], [vector2])[0][0]

    print(f"\n=== GLOBAL SIMILARITY: {similarity:.3f} ===")
    print("(1.0 = identical, 0.0 = completely different)")

    # Detailed feature comparison
    print(f"\n=== DETAILED COMPARISON ===")

    categories = ['rhythm', 'harmony', 'energy', 'spectral', 'frequency']

    for category in categories:
        print(f"\n{category.upper()}:")
        features1 = analysis1[category]
        features2 = analysis2[category]

        for key in features1.keys():
            val1 = features1[key]
            val2 = features2[key]
            diff = abs(val1 - val2)

            if category == 'rhythm' and key == 'tempo':
                diff_pct = diff / max(val1, val2) * 100
                print(f"  {key}: {val1:.1f} vs {val2:.1f} (±{diff:.1f} BPM, {diff_pct:.1f}% diff)")
            elif key in ['chroma_variance', 'energy_range', 'mid_low_ratio']:
                diff_pct = diff / max(val1, val2, 0.001) * 100 if max(val1, val2) > 0 else 0
                print(f"  {key}: {val1:.3f} vs {val2:.3f} (±{diff:.3f}, {diff_pct:.1f}% diff)")
            else:
                print(f"  {key}: {val1:.3f} vs {val2:.3f} (±{diff:.3f})")

    # Identify biggest differences
    print(f"\n=== BIGGEST DIFFERENCES ===")
    feature_names = [
        'tempo', 'onset_density', 'syncopation_level', 'chroma_variance',
        'energy_range', 'avg_brightness', 'mid_low_ratio'
    ]

    differences = []
    for i, name in enumerate(feature_names):
        if i < len(vector1):
            diff = abs(vector1[i] - vector2[i])
            differences.append((name, diff, vector1[i], vector2[i]))

    # Sort by difference size
    differences.sort(key=lambda x: x[1], reverse=True)

    for name, diff, val1, val2 in differences[:5]:
        print(f"  {name}: {val1:.3f} vs {val2:.3f} (diff: {diff:.3f})")

    return {
        'similarity': similarity,
        'analysis1': analysis1,
        'analysis2': analysis2,
        'vector1': vector1,
        'vector2': vector2,
        'differences': differences
    }


# Techno sketch vs Techno 1min - With Normalization

In [13]:
# STATS from before without decent Normalization:

# === GLOBAL SIMILARITY: 0.990 ===
# (1.0 = identical, 0.0 = completely different)

# === DETAILED COMPARISON ===

# RHYTHM:
#   tempo: 136.0 vs 90.7 (±45.3 BPM, 33.3% diff)
#   onset_density: 7.186 vs 6.128 (±1.058)
#   syncopation_level: 0.290 vs 0.246 (±0.044)
#   rhythmic_variance: 0.002 vs 0.003 (±0.001)
#   beat_strength: 0.869 vs 0.786 (±0.083)

# HARMONY:
#   chroma_variance: 0.045 vs 0.018 (±0.027, 59.1% diff)
#   key_strength: 1.791 vs 2.176 (±0.385)
#   harmonic_change_rate: 0.001 vs 0.001 (±0.000)
#   tonal_stability: 0.859 vs 0.760 (±0.098)

# ENERGY:
#   energy_range: 0.359 vs 0.497 (±0.138, 27.8% diff)
#   avg_energy: 0.160 vs 0.372 (±0.212)
#   energy_trend: -0.000 vs 0.000 (±0.000)
#   peak_density: 13.499 vs 16.471 (±2.972)

# SPECTRAL:
#   avg_brightness: 1392.691 vs 2065.275 (±672.583)
#   brightness_variance: 1298534.260 vs 1130691.420 (±167842.840)
#   avg_rolloff: 2788.004 vs 4850.429 (±2062.425)
#   avg_bandwidth: 1919.778 vs 2573.673 (±653.895)

# FREQUENCY:
#   low_proportion: 0.871 vs 0.947 (±0.076)
#   mid_proportion: 0.115 vs 0.031 (±0.084)
#   high_proportion: 0.014 vs 0.022 (±0.008)
#   mid_low_ratio: 0.132 vs 0.033 (±0.100, 75.2% diff)
#   high_mid_ratio: 0.121 vs 0.695 (±0.575)

# === BIGGEST DIFFERENCES ===
#   onset_density: 7.186 vs 6.128 (diff: 1.058)
#   avg_brightness: 1.791 vs 2.176 (diff: 0.385)
#   tempo: 0.680 vs 0.453 (diff: 0.227)
#   syncopation_level: 0.290 vs 0.246 (diff: 0.044)
#   energy_range: 0.045 vs 0.018 (diff: 0.027)


results = compare_global_features(full_path, short_ref_full_path)

Extracting global features...
Track 1: 59.6s
Track 2: 59.6s

=== GLOBAL SIMILARITY: 0.926 ===
(1.0 = identical, 0.0 = completely different)

=== DETAILED COMPARISON ===

RHYTHM:
  tempo: 136.0 vs 90.7 (±45.3 BPM, 33.3% diff)
  onset_density: 7.186 vs 6.128 (±1.058)
  syncopation_level: 0.290 vs 0.246 (±0.044)
  rhythmic_variance: 0.002 vs 0.003 (±0.001)
  beat_strength: 0.869 vs 0.786 (±0.083)

HARMONY:
  chroma_variance: 0.045 vs 0.018 (±0.027, 59.1% diff)
  key_strength: 1.791 vs 2.176 (±0.385)
  harmonic_change_rate: 0.001 vs 0.001 (±0.000)
  tonal_stability: 0.859 vs 0.760 (±0.098)

ENERGY:
  energy_range: 0.359 vs 0.497 (±0.138, 27.8% diff)
  avg_energy: 0.160 vs 0.372 (±0.212)
  energy_trend: -0.000 vs 0.000 (±0.000)
  peak_density: 13.499 vs 16.471 (±2.972)

SPECTRAL:
  avg_brightness: 1392.691 vs 2065.275 (±672.583)
  brightness_variance: 1298534.260 vs 1130691.420 (±167842.840)
  avg_rolloff: 2788.004 vs 4850.429 (±2062.425)
  avg_bandwidth: 1919.778 vs 2573.673 (±653.895)

FR

# Techno vs Piano music - Normalized

In [14]:
results = compare_global_features(full_path5, short_ref_full_path)

Extracting global features...
Track 1: 313.9s
Track 2: 59.6s

=== GLOBAL SIMILARITY: 0.362 ===
(1.0 = identical, 0.0 = completely different)

=== DETAILED COMPARISON ===

RHYTHM:
  tempo: 100.3 vs 90.7 (±9.7 BPM, 9.6% diff)
  onset_density: 2.342 vs 6.128 (±3.787)
  syncopation_level: 0.279 vs 0.246 (±0.033)
  rhythmic_variance: 0.351 vs 0.003 (±0.348)
  beat_strength: 0.273 vs 0.786 (±0.512)

HARMONY:
  chroma_variance: 0.078 vs 0.018 (±0.060, 76.4% diff)
  key_strength: 1.626 vs 2.176 (±0.550)
  harmonic_change_rate: 0.000 vs 0.001 (±0.001)
  tonal_stability: 0.887 vs 0.760 (±0.127)

ENERGY:
  energy_range: 0.156 vs 0.497 (±0.340, 68.5% diff)
  avg_energy: 0.035 vs 0.372 (±0.337)
  energy_trend: -0.000 vs 0.000 (±0.000)
  peak_density: 16.229 vs 16.471 (±0.242)

SPECTRAL:
  avg_brightness: 762.330 vs 2065.275 (±1302.945)
  brightness_variance: 55400.016 vs 1130691.420 (±1075291.404)
  avg_rolloff: 1285.839 vs 4850.429 (±3564.590)
  avg_bandwidth: 935.937 vs 2573.673 (±1637.735)

FREQ

# Techno vs Broken Beat - Normalized

In [15]:
results = compare_global_features(full_path4, short_ref_full_path)

Extracting global features...
Track 1: 508.2s
Track 2: 59.6s

=== GLOBAL SIMILARITY: 0.787 ===
(1.0 = identical, 0.0 = completely different)

=== DETAILED COMPARISON ===

RHYTHM:
  tempo: 118.8 vs 90.7 (±28.1 BPM, 23.7% diff)
  onset_density: 4.360 vs 6.128 (±1.768)
  syncopation_level: 0.320 vs 0.246 (±0.074)
  rhythmic_variance: 0.065 vs 0.003 (±0.062)
  beat_strength: 0.508 vs 0.786 (±0.278)

HARMONY:
  chroma_variance: 0.071 vs 0.018 (±0.053, 74.0% diff)
  key_strength: 1.444 vs 2.176 (±0.732)
  harmonic_change_rate: 0.000 vs 0.001 (±0.001)
  tonal_stability: 0.883 vs 0.760 (±0.123)

ENERGY:
  energy_range: 0.420 vs 0.497 (±0.077, 15.4% diff)
  avg_energy: 0.150 vs 0.372 (±0.222)
  energy_trend: 0.000 vs 0.000 (±0.000)
  peak_density: 7.024 vs 16.471 (±9.447)

SPECTRAL:
  avg_brightness: 1574.962 vs 2065.275 (±490.313)
  brightness_variance: 444594.495 vs 1130691.420 (±686096.925)
  avg_rolloff: 2808.663 vs 4850.429 (±2041.766)
  avg_bandwidth: 1479.268 vs 2573.673 (±1094.404)

FRE

In [16]:
results = compare_global_features(full_path11, short_ref_full_path)

Extracting global features...
Track 1: 421.1s
Track 2: 59.6s

=== GLOBAL SIMILARITY: 0.920 ===
(1.0 = identical, 0.0 = completely different)

=== DETAILED COMPARISON ===

RHYTHM:
  tempo: 88.3 vs 90.7 (±2.3 BPM, 2.6% diff)
  onset_density: 5.948 vs 6.128 (±0.180)
  syncopation_level: 0.227 vs 0.246 (±0.019)
  rhythmic_variance: 0.006 vs 0.003 (±0.003)
  beat_strength: 0.906 vs 0.786 (±0.121)

HARMONY:
  chroma_variance: 0.059 vs 0.018 (±0.040, 68.6% diff)
  key_strength: 1.927 vs 2.176 (±0.249)
  harmonic_change_rate: 0.000 vs 0.001 (±0.001)
  tonal_stability: 0.839 vs 0.760 (±0.079)

ENERGY:
  energy_range: 0.162 vs 0.497 (±0.335, 67.4% diff)
  avg_energy: 0.062 vs 0.372 (±0.310)
  energy_trend: 0.000 vs 0.000 (±0.000)
  peak_density: 11.447 vs 16.471 (±5.024)

SPECTRAL:
  avg_brightness: 2742.893 vs 2065.275 (±677.619)
  brightness_variance: 1332297.795 vs 1130691.420 (±201606.375)
  avg_rolloff: 5813.075 vs 4850.429 (±962.646)
  avg_bandwidth: 2658.949 vs 2573.673 (±85.276)

FREQUEN

## Our complex feature vector seems to be showing good similarity distant now between genres on a global scale.

But I'd like to try to simplify it and see what happens to our score.

In [29]:
def create_simplified_vector(analysis):
    """Create 5-feature vector with the most discriminating features"""

    vector = np.array([
        # Most discriminating features from your tests:
        analysis['harmony']['chroma_variance'] / 0.1,      # Biggest diff: piano vs techno
        analysis['energy']['energy_range'],                 # Good genre separator
        analysis['rhythm']['onset_density'] / 15.0,         # Electronic vs acoustic
        min(analysis['frequency']['mid_low_ratio'], 0.5) / 0.5,       # Frequency balance
        analysis['rhythm']['tempo'] / 200.0                 # Still important baseline
    ])

    return vector

In [30]:
def compare_simplified_features(track1_file, track2_file):
    """Compare tracks using only 5 key features"""

    analysis1 = extract_global_features(track1_file)
    analysis2 = extract_global_features(track2_file)

    vector1 = create_simplified_vector(analysis1)
    vector2 = create_simplified_vector(analysis2)

    similarity = cosine_similarity([vector1], [vector2])[0][0]

    print(f"SIMPLIFIED SIMILARITY (5 features): {similarity:.3f}")
    return vector1, vector2, similarity

In [31]:
compare_simplified_features(full_path, short_ref_full_path)

SIMPLIFIED SIMILARITY (5 features): 0.923


(array([0.45045745, 0.35860693, 0.47907529, 0.26496151, 0.67999589]),
 array([0.18421794, 0.49653849, 0.4085572 , 0.0658149 , 0.45333059]),
 np.float64(0.9229389610666344))

In [32]:
compare_simplified_features(full_path5, short_ref_full_path)

SIMPLIFIED SIMILARITY (5 features): 0.536


(array([0.77991241, 0.15625598, 0.15610694, 0.9105019 , 0.50174454]),
 array([0.18421794, 0.49653849, 0.4085572 , 0.0658149 , 0.45333059]),
 np.float64(0.5356115648326057))

In [28]:
compare_simplified_features(full_path4, short_ref_full_path)

SIMPLIFIED SIMILARITY (5 features): 0.747


(array([0.70940942, 0.41999078, 0.29067899, 0.72109365, 0.5940194 ]),
 array([0.18421794, 0.49653849, 0.4085572 , 0.0658149 , 0.45333059]),
 np.float64(0.7469054544615144))

Are simplied global features seems to be much less useful I think we should stick to 19 in our global variable and then maybe construct some aggegates ones for each musical paradigm that will be used more for feedback, the global one is better for our search maybe.

# Lets consider how to make feature extraction for the dimensions we wanna consider for feedback comparison.

In [33]:
def extract_feedback_features(analysis):
    """
    Extract focused feature sets for specific feedback categories.
    Takes the output from extract_global_features() and returns
    organized features for targeted advice generation.
    """

    feedback_features = {
        'eq': {
            # Frequency balance and tonal characteristics
            'brightness': analysis['spectral']['avg_brightness'],           # Hz - spectral centroid
            'brightness_variance': analysis['spectral']['brightness_variance'], # How much brightness changes
            'low_proportion': analysis['frequency']['low_proportion'],       # 0-1 - bass content
            'mid_proportion': analysis['frequency']['mid_proportion'],       # 0-1 - mid content
            'high_proportion': analysis['frequency']['high_proportion'],     # 0-1 - high content
            'rolloff_frequency': analysis['spectral']['avg_rolloff'],       # Hz - where highs roll off
            'spectral_bandwidth': analysis['spectral']['avg_bandwidth'],    # Hz - frequency spread
            'mid_low_ratio': analysis['frequency']['mid_low_ratio'],        # Ratio - mid vs bass balance
            'high_mid_ratio': analysis['frequency']['high_mid_ratio']       # Ratio - high vs mid balance
        },

        'energy': {
            # Dynamics, loudness, and energy characteristics
            'dynamic_range': analysis['energy']['energy_range'],           # 0-1 - difference between loud/quiet
            'average_energy': analysis['energy']['avg_energy'],            # 0-1 - overall loudness level
            'energy_trend': analysis['energy']['energy_trend'],            # Slope - building vs fading
            'peak_density': analysis['energy']['peak_density'],            # Per second - energy peaks
            'beat_strength': analysis['rhythm']['beat_strength']           # 0-1 - how strong the beats are
        },

        'rhythm': {
            # Timing, groove, and rhythmic complexity
            'tempo': analysis['rhythm']['tempo'],                          # BPM - song speed
            'onset_density': analysis['rhythm']['onset_density'],          # Per second - how many hits
            'syncopation_level': analysis['rhythm']['syncopation_level'],  # 0-1 - rhythmic complexity
            'rhythmic_variance': analysis['rhythm']['rhythmic_variance'],  # Timing consistency
            'beat_strength': analysis['rhythm']['beat_strength']           # 0-1 - groove strength
        },
    }

    return feedback_features

In [37]:
track_info = extract_global_features(full_path)

a = extract_feedback_features(track_info)

In [38]:
track_info = extract_global_features(short_ref_full_path)

b = extract_feedback_features(track_info)

In [39]:
def compare_feedback_features(user_features, reference_features, category):
    """
    Compare features within a specific feedback category.

    Args:
        user_features: Output from extract_feedback_features() for user track
        reference_features: Output from extract_feedback_features() for reference track
        category: 'eq', 'energy', 'rhythm', or 'arrangement'

    Returns:
        Dict with feature differences and recommendations
    """

    if category not in user_features or category not in reference_features:
        return {"error": f"Category '{category}' not found in feature data"}

    user_cat = user_features[category]
    ref_cat = reference_features[category]

    comparison = {}

    for feature_name in user_cat.keys():
        if feature_name in ref_cat:
            user_val = user_cat[feature_name]
            ref_val = ref_cat[feature_name]
            diff = user_val - ref_val
            percent_diff = (diff / ref_val * 100) if ref_val != 0 else 0

            comparison[feature_name] = {
                'user_value': user_val,
                'reference_value': ref_val,
                'difference': diff,
                'percent_difference': percent_diff
            }

    return comparison

In [40]:
compare_feedback_features(a, b, "energy")

{'dynamic_range': {'user_value': np.float32(0.35860693),
  'reference_value': np.float32(0.4965385),
  'difference': np.float32(-0.13793156),
  'percent_difference': np.float32(-27.778622)},
 'average_energy': {'user_value': np.float32(0.16004652),
  'reference_value': np.float32(0.37212026),
  'difference': np.float32(-0.21207374),
  'percent_difference': np.float32(-56.990646)},
 'energy_trend': {'user_value': np.float64(-5.924279110605449e-06),
  'reference_value': np.float64(4.05200260552251e-06),
  'difference': np.float64(-9.976281716127959e-06),
  'percent_difference': np.float64(-246.20620190449034)},
 'peak_density': {'user_value': 13.499177631578949,
  'reference_value': 16.471011513157897,
  'difference': -2.9718338815789487,
  'percent_difference': -18.042813455657498},
 'beat_strength': {'user_value': np.float32(0.8689674),
  'reference_value': np.float32(0.78560853),
  'difference': np.float32(0.083358884),
  'percent_difference': np.float32(10.610741)}}

#Chunking & Section seperation - COME BACK TO THIS END OF WEEK 1/START OF WEEK 2


### Below is come code inspired by the repo. It looks at how we can chunk using NMF. This is another option that we could explore instead of fine tuning the network. Id suggest to come back to this after I have the basic rag setup in the repo.
### https://github.com/dennisvdang/chorus-detection

> Add blockquote



In [46]:
# STRUCTURAL SEGMENTATION - CORE FUNCTIONS
#
# This module contains the foundational functions for automatic music structure analysis.
# These functions work together to identify section boundaries (intro, verse, chorus, etc.)
# in audio tracks using Non-negative Matrix Factorization (NMF) and beat-synchronized analysis.
#
# Key Functions:
# - create_beat_grid(): Creates regular beat grid for tempo-synchronized analysis
# - calculate_rms_energy(): Computes normalized energy levels over time
# - find_optimal_n_components(): Uses NMF to determine optimal number of musical sections
# - process_bound_times(): Cleans up detected section boundaries and converts to timestamps
#
# This module is imported by the main structural analysis pipeline.

import numpy as np
from sklearn.preprocessing import MinMaxScaler
from sklearn.decomposition import NMF
from scipy.ndimage import gaussian_filter1d

def create_beat_grid(beats: np.ndarray, tempo: float, sr: int, hop_length: int, duration: float, unit: str = 'time') -> np.ndarray:
    """Generate beat grid within the duration of a song. Returns beat grid in time units"""
    first_beat_time = librosa.frames_to_time(beats[0], sr=sr, hop_length=hop_length)
    seconds_per_beat = 60.0 / tempo
    num_beats_forward = int((duration - first_beat_time) / seconds_per_beat)
    num_beats_backward = int(first_beat_time / seconds_per_beat) + 1
    beat_times_forward = first_beat_time + np.arange(num_beats_forward) * seconds_per_beat
    beat_times_backward = first_beat_time - np.arange(1, num_beats_backward) * seconds_per_beat
    beat_grid = np.concatenate((np.array([0.0]), beat_times_backward[::-1], beat_times_forward))
    if unit == 'frames':
        beat_grid = librosa.time_to_frames(beat_grid, sr=sr, hop_length=hop_length)
    return beat_grid

def calculate_rms_energy(y: np.ndarray, hop_length: int) -> np.ndarray:
    """Calculate the RMS energy for each frame of the given audio waveform."""
    S, _ = librosa.magphase(librosa.stft(y, hop_length=hop_length))
    rms = librosa.feature.rms(S=S, hop_length=hop_length)[0]
    rms_normalized = (rms - np.min(rms)) / (np.max(rms) - np.min(rms))
    return rms_normalized

def find_optimal_n_components(X, random_state=None, plot_reconstruction_error=False):
    """
    Find the optimal number of components for NMF by minimizing the reconstruction error with a penalty term.
    Plots the reconstruction error and the score (reconstruction error + penalty)
    over different values of n_components.
    """
    n_features = X.shape[1]
    max_components = n_features
    reconstruction_errors = []
    scores = []

    # Calculate the penalty weight
    nmf = NMF(n_components=1, random_state=random_state, max_iter=5000, init='nndsvd')
    W = nmf.fit_transform(X)
    H = nmf.components_
    X_approx = W @ H
    reconstruction_error_1 = np.sum((X - X_approx) ** 2)
    penalty_weight = np.abs(reconstruction_error_1 / max_components)

    for n_components in range(1, max_components + 1):
        nmf = NMF(n_components=n_components, random_state=random_state, max_iter=5000, init='nndsvd')
        W = nmf.fit_transform(X)
        H = nmf.components_
        X_approx = W @ H
        reconstruction_error = np.sum((X - X_approx) ** 2)
        penalty = n_components * penalty_weight
        score = reconstruction_error + penalty
        reconstruction_errors.append(reconstruction_error)
        scores.append(score)

    # Plot reconstruction error and score over n_components
    if plot_reconstruction_error == True:
        fig, (ax1, ax2) = plt.subplots(2, 1, figsize=(10, 8))

        ax1.plot(range(1, max_components + 1), reconstruction_errors)
        ax1.set_xlabel('Number of Components')
        ax1.set_ylabel('Reconstruction Error')
        ax1.set_title('Reconstruction Error vs. Number of Components')

        ax2.plot(range(1, max_components + 1), scores)
        ax2.set_xlabel('Number of Components')
        ax2.set_ylabel('Score (Reconstruction Error + Penalty)')
        ax2.set_title('Score vs. Number of Components')

        plt.tight_layout()
        plt.show()

    # Find the optimal number of components
    optimal_n_components = np.argmin(scores) + 1
    # print(f"Optimal number of components: {optimal_n_components}")

    return optimal_n_components

def process_bound_times(bounds, beat_grid_times, duration):
    """
    Process the bounds indices and convert them to times using beat_grid_times.
    Include 0.0 as the starting time and the song duration as the ending time.
    Remove the second bound if the first bound is 0 and the difference between the first and second bounds is <= 7.
    If the difference between the last and second-to-last bound times is <= 8, merge the last bound with the second-to-last bound.
    """
    # Remove the second bound if the first bound is 0 and the difference between the first and second bounds is <= 7
    if bounds[0] == 0 and bounds[1] - bounds[0] <= 7:
        bounds = bounds[:1] + bounds[2:]

    # Convert bounds indices to times
    bound_times = [beat_grid_times[idx] for idx in bounds]

    # Include 0.0 as the starting time and the song duration as the ending time
    if bound_times[0] != 0:
        bound_times = [0.0] + bound_times + [duration]
    else:
        bound_times = bound_times + [duration]

    # Merge the last bound with the second-to-last bound if the difference between them is <= 8
    if len(bound_times) > 2 and bound_times[-1] - bound_times[-2] <= 8:
        bound_times = bound_times[:-2] + bound_times[-1:]

    return bound_times


In [47]:
# STRUCTURAL ANALYSIS - MAIN PIPELINE
#
# This module performs comprehensive structural segmentation of audio tracks to identify
# distinct musical sections (intro, verse, chorus, bridge, etc.) for arrangement analysis.
#
# Analysis Pipeline:
# 1. Audio preprocessing (harmonic/percussive separation, silence trimming)
# 2. Beat tracking and tempo detection
# 3. Multi-dimensional feature extraction (rhythm, energy, spectral, timbral)
# 4. NMF-based analysis to find optimal section boundaries
# 5. Harmonic analysis (when meaningful chord progressions detected)
# 6. Hybrid rhythm+harmony segmentation for complex tracks
#
# Features Extracted:
# - Rhythmic: Onset strength, frequency-band specific onsets (kick/snare/hihat)
# - Energy: RMS levels, dynamic range
# - Spectral: Brightness, timbral characteristics (MFCCs)
# - Harmonic: Chroma features for chord progression analysis
#
# Output: Section boundaries with timestamps for arrangement feedback system
#
# Requires: Core functions from structural segmentation module

# Constants
hop_length = 128
sr = 12000

audio_file = ref_full_path

# Load audio properly - your file is fine!
y, _ = librosa.load(audio_file, sr=sr)

# Optional: Trim silence for cleaner analysis (recommended)
y_trimmed, _ = librosa.effects.trim(y, top_db=30)
y = y_trimmed  # Use trimmed version

# Separate harmonic and percussive components
y_harm, y_perc = librosa.effects.hpss(y)

# Calculate duration correctly
duration = float(librosa.get_duration(y=y, sr=sr))
print(f"Track duration: {duration:.2f} seconds ({duration/60:.1f} minutes)")

# Beat tracking
onset_env = librosa.onset.onset_strength(y=y_perc, sr=sr, hop_length=hop_length)
tempo, beats = librosa.beat.beat_track(onset_envelope=onset_env, sr=sr, hop_length=hop_length)

# Ensure tempo is scalar and fix the create_beat_grid function calls
tempo = float(tempo) if hasattr(tempo, '__len__') else float(tempo)

# Fix for create_beat_grid - make sure it handles scalars properly
def create_beat_grid_fixed(beats: np.ndarray, tempo: float, sr: int, hop_length: int, duration: float, unit: str = 'time') -> np.ndarray:
    """Generate beat grid within the duration of a song. Fixed version."""
    # Ensure all inputs are scalars
    first_beat_time = float(librosa.frames_to_time(beats[0], sr=sr, hop_length=hop_length))
    seconds_per_beat = 60.0 / float(tempo)
    duration = float(duration)

    num_beats_forward = int((duration - first_beat_time) / seconds_per_beat)
    num_beats_backward = int(first_beat_time / seconds_per_beat) + 1

    beat_times_forward = first_beat_time + np.arange(num_beats_forward) * seconds_per_beat
    beat_times_backward = first_beat_time - np.arange(1, num_beats_backward) * seconds_per_beat
    beat_grid = np.concatenate((np.array([0.0]), beat_times_backward[::-1], beat_times_forward))

    if unit == 'frames':
        beat_grid = librosa.time_to_frames(beat_grid, sr=sr, hop_length=hop_length)
    return beat_grid

# Create beat grids with fixed function
beat_grid_frames = create_beat_grid_fixed(beats, tempo, sr, hop_length, duration, unit='frames')
beat_grid_times = create_beat_grid_fixed(beats, tempo, sr, hop_length, duration, unit='time')

print(f"Detected tempo: {tempo:.1f} BPM")
print(f"Beat grid has {len(beat_grid_times)} beats")

# =============================================================================
# RHYTHMIC AND ENERGY FEATURES
# =============================================================================

# 1. Onset Strength (rhythmic complexity)
onset_strength = librosa.onset.onset_strength(y=y_perc, sr=sr, hop_length=hop_length)
onset_sync = librosa.util.sync(onset_strength.reshape(1, -1), beat_grid_frames, aggregate=np.mean)

# 2. RMS Energy (overall energy levels)
rms_energy = calculate_rms_energy(y, hop_length=hop_length)
rms_sync = librosa.util.sync(rms_energy.reshape(1, -1), beat_grid_frames, aggregate=np.mean)

# 3. Spectral Centroid (brightness/timbre changes)
spectral_centroid = librosa.feature.spectral_centroid(y=y, sr=sr, hop_length=hop_length)[0]
spectral_centroid_norm = (spectral_centroid - np.min(spectral_centroid)) / (np.max(spectral_centroid) - np.min(spectral_centroid))
centroid_sync = librosa.util.sync(spectral_centroid_norm.reshape(1, -1), beat_grid_frames, aggregate=np.mean)

# 4. MFCC Features (timbral characteristics)
mfccs = librosa.feature.mfcc(y=y, sr=sr, hop_length=hop_length, n_mfcc=5)
mfccs_norm = MinMaxScaler().fit_transform(mfccs.T).T
mfccs_sync = librosa.util.sync(mfccs_norm, beat_grid_frames, aggregate=np.mean)

# 5. Frequency-band specific rhythmic features
def extract_rhythmic_features(y_perc, sr, hop_length, beat_grid_frames):
    """Extract features that capture rhythmic complexity and subdivision patterns"""

    S = np.abs(librosa.stft(y_perc, hop_length=hop_length))
    freq_bins = librosa.fft_frequencies(sr=sr, n_fft=2048)

    # Low frequency onsets (kick drum region: 20-120 Hz)
    low_freq_mask = (freq_bins >= 20) & (freq_bins <= 120)
    if np.any(low_freq_mask):
        low_onsets = librosa.onset.onset_strength(S=S[low_freq_mask], sr=sr, hop_length=hop_length)
    else:
        low_onsets = np.zeros(S.shape[1])

    # Mid frequency onsets (snare/clap region: 200-2000 Hz)
    mid_freq_mask = (freq_bins >= 200) & (freq_bins <= 2000)
    if np.any(mid_freq_mask):
        mid_onsets = librosa.onset.onset_strength(S=S[mid_freq_mask], sr=sr, hop_length=hop_length)
    else:
        mid_onsets = np.zeros(S.shape[1])

    # High frequency onsets (hi-hats: adjust for sr=12000)
    high_freq_threshold = min(4000, sr // 3)  # Max ~4000Hz for sr=12000
    high_freq_mask = freq_bins >= high_freq_threshold
    if np.any(high_freq_mask):
        high_onsets = librosa.onset.onset_strength(S=S[high_freq_mask], sr=sr, hop_length=hop_length)
    else:
        high_onsets = np.zeros(S.shape[1])

    # Sync to beat grid
    low_onsets_sync = librosa.util.sync(low_onsets.reshape(1, -1), beat_grid_frames, aggregate=np.mean)
    mid_onsets_sync = librosa.util.sync(mid_onsets.reshape(1, -1), beat_grid_frames, aggregate=np.mean)
    high_onsets_sync = librosa.util.sync(high_onsets.reshape(1, -1), beat_grid_frames, aggregate=np.mean)

    return low_onsets_sync, mid_onsets_sync, high_onsets_sync

low_onsets_sync, mid_onsets_sync, high_onsets_sync = extract_rhythmic_features(y_perc, sr, hop_length, beat_grid_frames)

# 6. Combine all features
rhythm_energy_features = np.vstack([
    onset_sync,           # Overall rhythmic activity
    rms_sync,            # Energy level
    centroid_sync,       # Brightness/timbre
    mfccs_sync,          # Timbral characteristics (5 dims)
    low_onsets_sync,     # Kick drum activity
    mid_onsets_sync,     # Snare/clap activity
    high_onsets_sync     # Hi-hat activity
])

# Normalize features
rhythm_energy_features = MinMaxScaler().fit_transform(rhythm_energy_features.T).T
print(f"Combined feature matrix shape: {rhythm_energy_features.shape}")

# =============================================================================
# NMF ANALYSIS
# =============================================================================

optimal_n_components_re = find_optimal_n_components(rhythm_energy_features.T, plot_reconstruction_error=False)
print(f"Optimal components for rhythm/energy features: {optimal_n_components_re}")

nmf_re = NMF(n_components=optimal_n_components_re, max_iter=5000, init='nndsvd')
rhythm_energy_acts = nmf_re.fit_transform(rhythm_energy_features.T).T

# Normalize activations
rhythm_energy_acts = (rhythm_energy_acts - rhythm_energy_acts.min(axis=1, keepdims=True)) / \
                     (rhythm_energy_acts.max(axis=1, keepdims=True) - rhythm_energy_acts.min(axis=1, keepdims=True))

# Smooth activations
rhythm_energy_acts_smooth = gaussian_filter1d(rhythm_energy_acts, sigma=1, axis=1)

# =============================================================================
# SEGMENTATION - APPROPRIATE FOR 1-MINUTE TRACKS
# =============================================================================

# For 1-minute tracks, use maximum 3 segments
max_segments = 3
print(f"Using max {max_segments} segments for {duration:.1f}s track")

# Segment using different representations
bounds_re_raw = librosa.segment.agglomerative(rhythm_energy_features, max_segments)
bounds_re_acts = librosa.segment.agglomerative(rhythm_energy_acts, max_segments)
bounds_re_smooth = librosa.segment.agglomerative(rhythm_energy_acts_smooth, max_segments)

# Convert to time boundaries
bound_times_re_raw = process_bound_times(bounds_re_raw, beat_grid_times, duration)
bound_times_re_acts = process_bound_times(bounds_re_acts, beat_grid_times, duration)
bound_times_re_smooth = process_bound_times(bounds_re_smooth, beat_grid_times, duration)

print("\n=== RHYTHM/ENERGY SEGMENTATION RESULTS ===")
print(f"Raw features: {len(bound_times_re_raw)-1} segments at times: {[f'{t:.1f}s' for t in bound_times_re_raw]}")
print(f"NMF activations: {len(bound_times_re_acts)-1} segments at times: {[f'{t:.1f}s' for t in bound_times_re_acts]}")
print(f"Smoothed activations: {len(bound_times_re_smooth)-1} segments at times: {[f'{t:.1f}s' for t in bound_times_re_smooth]}")

# =============================================================================
# HARMONIC ANALYSIS (optional)
# =============================================================================

chromagram = librosa.feature.chroma_cqt(y=y_harm, sr=sr, hop_length=hop_length, bins_per_octave=24)
chroma_sync = librosa.util.sync(chromagram, beat_grid_frames, aggregate=np.mean)
chroma_sync = MinMaxScaler().fit_transform(chroma_sync.T).T

chroma_variance = np.var(chroma_sync, axis=1).mean()
print(f"\nChroma variance (harmonic complexity): {chroma_variance:.4f}")

if chroma_variance > 0.01:
    print("Sufficient harmonic content detected - running chroma analysis...")

    optimal_n_components_chroma = find_optimal_n_components(chroma_sync.T, plot_reconstruction_error=False)
    nmf_chroma = NMF(n_components=optimal_n_components_chroma, max_iter=5000, init='nndsvd')
    chroma_acts = nmf_chroma.fit_transform(chroma_sync.T).T
    chroma_acts = (chroma_acts - chroma_acts.min(axis=1, keepdims=True)) / \
                  (chroma_acts.max(axis=1, keepdims=True) - chroma_acts.min(axis=1, keepdims=True))

    bounds_chroma = librosa.segment.agglomerative(chroma_acts, max_segments)
    bound_times_chroma = process_bound_times(bounds_chroma, beat_grid_times, duration)

    print(f"Chroma-based: {len(bound_times_chroma)-1} segments at times: {[f'{t:.1f}s' for t in bound_times_chroma]}")

    # Optional hybrid analysis
    if chroma_variance > 0.02:  # Only if significant harmonic content
        hybrid_features = np.vstack([rhythm_energy_features, chroma_sync])
        hybrid_features = MinMaxScaler().fit_transform(hybrid_features.T).T

        optimal_n_hybrid = find_optimal_n_components(hybrid_features.T, plot_reconstruction_error=False)
        nmf_hybrid = NMF(n_components=optimal_n_hybrid, max_iter=5000, init='nndsvd')
        hybrid_acts = nmf_hybrid.fit_transform(hybrid_features.T).T
        hybrid_acts = (hybrid_acts - hybrid_acts.min(axis=1, keepdims=True)) / \
                      (hybrid_acts.max(axis=1, keepdims=True) - hybrid_acts.min(axis=1, keepdims=True))
        hybrid_acts_smooth = gaussian_filter1d(hybrid_acts, sigma=1, axis=1)

        bounds_hybrid = librosa.segment.agglomerative(hybrid_acts_smooth, max_segments)
        bound_times_hybrid = process_bound_times(bounds_hybrid, beat_grid_times, duration)

        print(f"Hybrid analysis: {len(bound_times_hybrid)-1} segments at times: {[f'{t:.1f}s' for t in bound_times_hybrid]}")

else:
    print("Low harmonic content - rhythm/energy analysis is most appropriate")

# =============================================================================
# FINAL RECOMMENDATIONS
# =============================================================================

print(f"\n=== ANALYSIS SUMMARY ===")
print(f"Track: {duration:.1f} seconds, {tempo:.1f} BPM")
print(f"Harmonic complexity: {chroma_variance:.4f}")

if chroma_variance > 0.03:
    print("HIGH harmonic variation - use hybrid approach")
elif chroma_variance > 0.01:
    print("MODERATE harmonic variation - rhythm/energy with harmonic validation")
else:
    print("LOW harmonic variation - pure rhythm/energy analysis")

print(f"\nRecommended segmentation:")
print(f"  Primary method: Smoothed rhythm/energy activations")
print(f"  Segments: {[f'{t:.1f}s' for t in bound_times_re_smooth]}")

# Calculate segment durations for context
segment_durations = [bound_times_re_smooth[i+1] - bound_times_re_smooth[i] for i in range(len(bound_times_re_smooth)-1)]
print(f"  Segment durations: {[f'{d:.1f}s' for d in segment_durations]}")

Track duration: 310.60 seconds (5.2 minutes)
Detected tempo: 137.2 BPM
Beat grid has 711 beats
Combined feature matrix shape: (11, 711)
Optimal components for rhythm/energy features: 4
Using max 3 segments for 310.6s track

=== RHYTHM/ENERGY SEGMENTATION RESULTS ===
Raw features: 3 segments at times: ['0.0s', '113.8s', '211.7s', '310.6s']
NMF activations: 3 segments at times: ['0.0s', '28.0s', '198.6s', '310.6s']
Smoothed activations: 3 segments at times: ['0.0s', '27.6s', '198.6s', '310.6s']

Chroma variance (harmonic complexity): 0.0240
Sufficient harmonic content detected - running chroma analysis...
Chroma-based: 3 segments at times: ['0.0s', '114.2s', '126.9s', '310.6s']
Hybrid analysis: 3 segments at times: ['0.0s', '114.2s', '127.3s', '310.6s']

=== ANALYSIS SUMMARY ===
Track: 310.6 seconds, 137.2 BPM
Harmonic complexity: 0.0240
MODERATE harmonic variation - rhythm/energy with harmonic validation

Recommended segmentation:
  Primary method: Smoothed rhythm/energy activations
  S

In [ ]:
# PRODUCTION FEEDBACK ANALYSIS
#
# This module provides detailed production and mixing analysis for electronic music tracks.
# It builds on structural segmentation results to give section-specific feedback on
# mixing, arrangement, and production quality.
#
# Analysis Components:
# 1. Energy Curve Analysis: Identifies energy peaks, valleys, and progression trends
# 2. Frequency Balance Analysis: Examines low/mid/high frequency distribution over time
# 3. Vocal Clarity Analysis: Focuses on vocal frequency ranges and potential masking issues
# 4. Rhythmic Complexity Analysis: Measures syncopation, groove, and rhythmic variation
# 5. Section-by-Section Analysis: Compares production characteristics across song sections
# 6. Production Feedback Generation: Converts analysis into actionable mixing/arrangement advice
#
# Output Examples:
# - "Your second section needs more high-frequency content for brightness"
# - "Consider reducing bass in the vocal frequency range to avoid masking"
# - "Track builds well over time with good energy progression"
# - "Rhythmic complexity is appropriate for the genre"
#
# This module works with section boundaries from structural analysis to provide
# targeted production feedback for each part of the track.
#
# Requires: Audio data and section boundaries from main structural analysis pipeline

print("=== PRODUCTION FEEDBACK ANALYSIS ===")

# 1. ENERGY CURVE ANALYSIS
def analyze_energy_curve(y, sr, hop_length, beat_grid_times):
    """Analyze how energy changes over time"""

    # Calculate RMS energy with smaller hop for more detail
    rms = librosa.feature.rms(y=y, hop_length=hop_length//2)[0]
    times = librosa.frames_to_time(np.arange(len(rms)), sr=sr, hop_length=hop_length//2)

    # Smooth for trend analysis
    from scipy.ndimage import gaussian_filter1d
    rms_smooth = gaussian_filter1d(rms, sigma=10)

    # Find energy peaks and valleys
    from scipy.signal import find_peaks
    peaks, _ = find_peaks(rms_smooth, height=np.mean(rms_smooth))
    valleys, _ = find_peaks(-rms_smooth, height=-np.mean(rms_smooth))

    return {
        'rms': rms,
        'times': times,
        'rms_smooth': rms_smooth,
        'peaks': peaks,
        'valleys': valleys,
        'energy_range': np.max(rms) - np.min(rms),
        'avg_energy': np.mean(rms)
    }

energy_analysis = analyze_energy_curve(y, sr, hop_length, beat_grid_times)

print(f"Energy Analysis:")
print(f"  - Energy range: {energy_analysis['energy_range']:.3f}")
print(f"  - Average energy: {energy_analysis['avg_energy']:.3f}")
print(f"  - Energy peaks at: {[f'{energy_analysis['times'][p]:.1f}s' for p in energy_analysis['peaks'][:5]]}")
print(f"  - Energy valleys at: {[f'{energy_analysis['times'][v]:.1f}s' for v in energy_analysis['valleys'][:5]]}")

# 2. FREQUENCY BALANCE ANALYSIS
def analyze_frequency_balance(y, sr, hop_length):
    """Analyze frequency content over time"""

    # Get spectrogram
    S = np.abs(librosa.stft(y, hop_length=hop_length))
    freqs = librosa.fft_frequencies(sr=sr)
    times = librosa.frames_to_time(np.arange(S.shape[1]), sr=sr, hop_length=hop_length)

    # Define frequency bands
    low_band = (freqs >= 20) & (freqs <= 250)    # Bass/kick
    mid_band = (freqs >= 250) & (freqs <= 2000)  # Vocals/snares
    high_band = (freqs >= 2000) & (freqs <= 8000) # Cymbals/air

    # Calculate energy in each band over time
    low_energy = np.mean(S[low_band], axis=0)
    mid_energy = np.mean(S[mid_band], axis=0)
    high_energy = np.mean(S[high_band], axis=0)

    # Calculate balance ratios
    mid_to_low = np.mean(mid_energy) / np.mean(low_energy)
    high_to_mid = np.mean(high_energy) / np.mean(mid_energy)

    return {
        'times': times,
        'low_energy': low_energy,
        'mid_energy': mid_energy,
        'high_energy': high_energy,
        'mid_to_low_ratio': mid_to_low,
        'high_to_mid_ratio': high_to_mid
    }

freq_analysis = analyze_frequency_balance(y, sr, hop_length)

print(f"\nFrequency Balance:")
print(f"  - Mid/Low ratio: {freq_analysis['mid_to_low_ratio']:.2f}")
print(f"  - High/Mid ratio: {freq_analysis['high_to_mid_ratio']:.2f}")

# 3. VOCAL CLARITY ANALYSIS
def analyze_vocal_clarity(y, sr, hop_length):
    """Analyze potential vocal masking issues"""

    # Focus on vocal frequency range (80-2000 Hz for most vocals)
    S = np.abs(librosa.stft(y, hop_length=hop_length))
    freqs = librosa.fft_frequencies(sr=sr)

    vocal_band = (freqs >= 80) & (freqs <= 2000)
    vocal_energy = S[vocal_band]

    # Calculate spectral centroid in vocal band (brightness)
    vocal_centroid = np.sum(vocal_energy * freqs[vocal_band].reshape(-1, 1), axis=0) / np.sum(vocal_energy, axis=0)

    # Calculate vocal clarity proxy (spectral flux in vocal band)
    vocal_flux = np.sum(np.diff(vocal_energy, axis=1)**2, axis=0)

    return {
        'vocal_centroid': vocal_centroid,
        'vocal_flux': vocal_flux,
        'avg_vocal_brightness': np.mean(vocal_centroid),
        'vocal_activity': np.mean(vocal_flux)
    }

vocal_analysis = analyze_vocal_clarity(y, sr, hop_length)

print(f"\nVocal Analysis:")
print(f"  - Average vocal brightness: {vocal_analysis['avg_vocal_brightness']:.1f} Hz")
print(f"  - Vocal activity level: {vocal_analysis['vocal_activity']:.3f}")

# 4. RHYTHMIC COMPLEXITY ANALYSIS
def analyze_rhythmic_complexity(y_perc, sr, hop_length, tempo):
    """Analyze rhythmic variation and complexity"""

    # Calculate onset strength
    onset_env = librosa.onset.onset_strength(y=y_perc, sr=sr, hop_length=hop_length)

    # Find actual onsets
    onsets = librosa.onset.onset_detect(onset_envelope=onset_env, sr=sr, hop_length=hop_length)
    onset_times = librosa.frames_to_time(onsets, sr=sr, hop_length=hop_length)

    # Calculate inter-onset intervals
    if len(onset_times) > 1:
        intervals = np.diff(onset_times)

        # Beat-relative analysis
        beat_duration = 60.0 / tempo
        beat_relative_intervals = intervals / beat_duration

        # Rhythmic complexity metrics
        interval_variance = np.var(intervals)
        syncopation_measure = np.sum(np.abs(beat_relative_intervals - np.round(beat_relative_intervals)))

    else:
        interval_variance = 0
        syncopation_measure = 0

    return {
        'num_onsets': len(onset_times),
        'interval_variance': interval_variance,
        'syncopation_measure': syncopation_measure,
        'onset_density': len(onset_times) / duration
    }

rhythm_analysis = analyze_rhythmic_complexity(y_perc, sr, hop_length, 137.0)  # Use correct BPM

print(f"\nRhythmic Analysis:")
print(f"  - Number of onsets: {rhythm_analysis['num_onsets']}")
print(f"  - Onset density: {rhythm_analysis['onset_density']:.2f} onsets/second")
print(f"  - Rhythmic variance: {rhythm_analysis['interval_variance']:.3f}")
print(f"  - Syncopation level: {rhythm_analysis['syncopation_measure']:.2f}")

# 5. SECTION-BY-SECTION ANALYSIS
def analyze_by_sections(bound_times, energy_analysis, freq_analysis):
    """Compare characteristics across sections"""

    sections = []
    for i in range(len(bound_times)-1):
        start_time = bound_times[i]
        end_time = bound_times[i+1]

        # Find indices for this section
        time_mask = (energy_analysis['times'] >= start_time) & (energy_analysis['times'] <= end_time)
        freq_time_mask = (freq_analysis['times'] >= start_time) & (freq_analysis['times'] <= end_time)

        if np.any(time_mask) and np.any(freq_time_mask):
            section_energy = np.mean(energy_analysis['rms'][time_mask])
            section_low = np.mean(freq_analysis['low_energy'][freq_time_mask])
            section_mid = np.mean(freq_analysis['mid_energy'][freq_time_mask])
            section_high = np.mean(freq_analysis['high_energy'][freq_time_mask])

            sections.append({
                'start': start_time,
                'end': end_time,
                'duration': end_time - start_time,
                'energy': section_energy,
                'low': section_low,
                'mid': section_mid,
                'high': section_high
            })

    return sections

# Use the smoothed boundaries from your previous analysis
bound_times_smooth = [0.0, 14.2, 27.9, 56.2]  # From your results
section_analysis = analyze_by_sections(bound_times_smooth, energy_analysis, freq_analysis)

print(f"\n=== SECTION COMPARISON ===")
for i, section in enumerate(section_analysis):
    print(f"Section {i+1} ({section['start']:.1f}s - {section['end']:.1f}s):")
    print(f"  Duration: {section['duration']:.1f}s")
    print(f"  Energy: {section['energy']:.3f}")
    print(f"  Low/Mid/High: {section['low']:.3f}/{section['mid']:.3f}/{section['high']:.3f}")

# 6. PRODUCTION FEEDBACK GENERATION
print(f"\n=== PRODUCTION FEEDBACK ===")

# Energy progression feedback
energy_trend = np.polyfit(range(len(energy_analysis['rms_smooth'])), energy_analysis['rms_smooth'], 1)[0]
if energy_trend > 0.001:
    print("✅ ENERGY: Good energy progression - track builds over time")
elif energy_trend < -0.001:
    print("⚠️  ENERGY: Energy decreases over time - consider building more excitement")
else:
    print("⚠️  ENERGY: Flat energy curve - could use more dynamic variation")

# Frequency balance feedback
if 0.8 <= freq_analysis['mid_to_low_ratio'] <= 2.0:
    print("✅ BALANCE: Good mid/low balance for vocals")
else:
    print(f"⚠️  BALANCE: Mid/low ratio is {freq_analysis['mid_to_low_ratio']:.2f} - consider adjusting vocal/bass balance")

if freq_analysis['high_to_mid_ratio'] < 0.3:
    print("⚠️  BRIGHTNESS: Track might sound dull - consider adding high-frequency content")
elif freq_analysis['high_to_mid_ratio'] > 1.5:
    print("⚠️  BRIGHTNESS: Track might sound harsh - consider taming highs")
else:
    print("✅ BRIGHTNESS: Good high-frequency balance")

# Rhythmic complexity feedback
if rhythm_analysis['syncopation_measure'] > 2.0:
    print("✅ RHYTHM: Good rhythmic complexity for booty techno")
elif rhythm_analysis['syncopation_measure'] < 0.5:
    print("⚠️  RHYTHM: Could use more rhythmic interest/syncopation")
else:
    print("✅ RHYTHM: Moderate rhythmic complexity")

# Section balance feedback
if len(section_analysis) >= 3:
    section_durations = [s['duration'] for s in section_analysis]
    if section_durations[-1] > sum(section_durations[:-1]):
        print("⚠️  STRUCTURE: Final section is very long - consider adding variation or splitting")
    else:
        print("✅ STRUCTURE: Good section balance")